<a href="https://colab.research.google.com/github/yuriao/API/blob/master/solafune_solarPanelDetection_LGBM_2.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
import glob
import tifffile
import numpy as np
import lightgbm as lgb
import warnings
import tqdm
from sklearn.metrics import f1_score
from sklearn.model_selection import KFold, StratifiedKFold, GroupKFold, train_test_split
import optuna
warnings.simplefilter('ignore')

### 1. read data

In [ ]:
train_path =  'D:/D_drive_proj/DS_projects/solafune_solarPanelDetection/train/s2_image'
mask_path = 'D:/D_drive_proj/DS_projects/solafune_solarPanelDetection/train/mask'

masks = glob.glob(f'{mask_path}/*')
trains = glob.glob(f'{train_path}/*')
masks.sort()
trains.sort()

In [ ]:
X = []
y = []
g = []

for i, (t, m) in enumerate(zip(trains, masks)):
    img = tifffile.imread(t).astype(float)
    mask = tifffile.imread(m).astype(float)
    X.append(img.reshape(-1,12))
    y.append(mask.reshape(-1))
    g.append(np.ones_like(mask.reshape(-1))*i)

X = np.vstack(X)
y = np.hstack(y)
g = np.hstack(g)

### 2. EDA: check nans in data

In [ ]:
print('# of nans in image = '+str(np.sum(np.isnan(X))))
print('# of nans in mask = '+str(np.sum(np.isnan(y))))

# of nans in image = 0
# of nans in mask = 0


### 3. training and testing utility functions

In [ ]:
def GroupKFold_model_training(X, y, g,lgb_params):
    gkfold = GroupKFold(n_splits=4)
    models = []
    for i, (train_idx, valid_idx) in enumerate(gkfold.split(X, y, g)):
        train_x = X[train_idx]
        train_y = y[train_idx]
        val_x = X[valid_idx]
        val_y = y[valid_idx]
        m = lgb.LGBMClassifier(**lgb_params)
        m.fit(train_x, train_y,
            eval_metric='logloss',
            eval_set=[(val_x, val_y)],
            callbacks=[
                lgb.log_evaluation(100),
            ],
        )
        models.append(m)

    return models

In [ ]:
def GroupKFold_model_test(X,models):
    pred = 0
    for model in models:
        pred = pred+model.predict_proba(X) / len(models)

    final_preds=[]
    for i in range(0,pred.shape[0]):
        if pred[i][0]>pred[i][1]:
            final_preds.append(0)
        else:
            final_preds.append(1)

    return final_preds


### 4. Hyperparameter tuning with Optuna

In [ ]:
def objective(trial):

    param = {
        'n_estimators': trial.suggest_int('n_estimators', 1,1000),
        'reg_alpha': trial.suggest_loguniform('reg_alpha', 1e-3, 10.0),
        'reg_lambda': trial.suggest_loguniform('reg_lambda', 1e-3, 10.0),
        'colsample_bytree': trial.suggest_categorical('colsample_bytree', [0.1,0.2,0.3,0.4,0.5,0.6,0.7,0.8,0.9, 1.0]),
        'subsample': trial.suggest_categorical('subsample', [0.1,0.2,0.3,0.4,0.5,0.6,0.7,0.8,1.0]),
        'learning_rate': trial.suggest_categorical('learning_rate', [0.00001,0.00005,0.001,0.005,0.01,0.02,0.05,0.1]),
        'max_depth': trial.suggest_int('max_depth', 1 , 200),
        'num_leaves' : trial.suggest_int('num_leaves', 1, 1000),
        'min_child_samples': trial.suggest_int('min_child_samples', 1, 300),
    }

    X_train,X_test,y_train,y_test,g_train,g_test=train_test_split(X,y,g,test_size=0.3,shuffle=True)
    models = GroupKFold_model_training(X_train,y_train,g_train,param)
    y_pred=GroupKFold_model_test(X_test,models)
    f= f1_score(y_test,y_pred)

    return f

In [ ]:
optuna.logging.set_verbosity(optuna.logging.CRITICAL)
study = optuna.create_study(direction='maximize')
#study.optimize(objective, n_trials=100)
#best_params=study.best_trial.params

[LightGBM] [Info] Number of positive: 56286, number of negative: 538676
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000959 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 3060
[LightGBM] [Info] Number of data points in the train set: 594962, number of used features: 12
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.094604 -> initscore=-2.258668
[LightGBM] [Info] Start training from score -2.258668
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best g

In [ ]:
best_params={'n_estimators': 748,
 'reg_alpha': 0.01033323111097222,
 'reg_lambda': 0.001696493306975717,
 'colsample_bytree': 1.0,
 'subsample': 0.8,
 'learning_rate': 0.1,
 'max_depth': 36,
 'num_leaves': 966,
 'min_child_samples': 20}

{'n_estimators': 748,
 'reg_alpha': 0.01033323111097222,
 'reg_lambda': 0.001696493306975717,
 'colsample_bytree': 1.0,
 'subsample': 0.8,
 'learning_rate': 0.1,
 'max_depth': 36,
 'num_leaves': 966,
 'min_child_samples': 20,
 'min_data_per_groups': 15}

### 5. training

In [ ]:
models = GroupKFold_model_training(X,y,g,best_params)

[LightGBM] [Warning] Unknown parameter: min_data_per_groups
[LightGBM] [Warning] Unknown parameter: min_data_per_groups
[LightGBM] [Info] Number of positive: 81882, number of negative: 768528
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.007940 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 3060
[LightGBM] [Info] Number of data points in the train set: 850410, number of used features: 12
[LightGBM] [Warning] Unknown parameter: min_data_per_groups
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.096285 -> initscore=-2.239198
[LightGBM] [Info] Start training from score -2.239198
[100]	valid_0's binary_logloss: 0.0868067
[200]	valid_0's binary_logloss: 0.0897498
[300]	valid_0's binary_logloss: 0.0945851
[400]	valid_0's binary_logloss: 0.1007
[500]	valid_0's binary_logloss: 0.107158
[600]	valid_0's binary_logloss: 0.114206
[700]	valid_0's binary_logloss: 0.121026
[LightGBM] [Warning] Unknown paramet

### 6. generate results

In [ ]:
test_path =  'D:/D_drive_proj/DS_projects/solafune_solarPanelDetection/evaluation'
test_mask_path = 'D:/D_drive_proj/DS_projects/solafune_solarPanelDetection/sample'

masks = glob.glob(f'{test_mask_path}/*')
tests = glob.glob(f'{test_path}/*')
masks.sort()
tests.sort()

In [ ]:
import os
if not os.path.isdir('D:/D_drive_proj/DS_projects/solafune_solarPanelDetection/output2'):
    os.mkdir('D:/D_drive_proj/DS_projects/solafune_solarPanelDetection/output2')

In [ ]:
threshold = 0.5

for i, (m, t) in tqdm.tqdm(enumerate(zip(masks, tests))):
    basename = os.path.basename(m)
    output_file = f'D:/D_drive_proj/DS_projects/solafune_solarPanelDetection/output2/{basename}'

    img = tifffile.imread(t).astype(float)
    mask = tifffile.imread(m).astype(float)

    X = img.reshape(-1, 12)
    shape_mask = mask.shape

    pred=GroupKFold_model_test(X,models)

    pred_mask = np.array(pred).astype(np.uint8)
    pred_mask = pred_mask.reshape(shape_mask[0], shape_mask[1])

    tifffile.imwrite(output_file, pred_mask)


3it [00:00, 29.10it/s]

[LightGBM] [Warning] Unknown parameter: min_data_per_groups
[LightGBM] [Warning] Unknown parameter: min_data_per_groups
[LightGBM] [Warning] Unknown parameter: min_data_per_groups
[LightGBM] [Warning] Unknown parameter: min_data_per_groups
[LightGBM] [Warning] Unknown parameter: min_data_per_groups
[LightGBM] [Warning] Unknown parameter: min_data_per_groups
[LightGBM] [Warning] Unknown parameter: min_data_per_groups
[LightGBM] [Warning] Unknown parameter: min_data_per_groups
[LightGBM] [Warning] Unknown parameter: min_data_per_groups
[LightGBM] [Warning] Unknown parameter: min_data_per_groups
[LightGBM] [Warning] Unknown parameter: min_data_per_groups
[LightGBM] [Warning] Unknown parameter: min_data_per_groups
[LightGBM] [Warning] Unknown parameter: min_data_per_groups
[LightGBM] [Warning] Unknown parameter: min_data_per_groups
[LightGBM] [Warning] Unknown parameter: min_data_per_groups
[LightGBM] [Warning] Unknown parameter: min_data_per_groups
[LightGBM] [Warning] Unknown parameter: 

11it [00:00, 33.64it/s]

[LightGBM] [Warning] Unknown parameter: min_data_per_groups
[LightGBM] [Warning] Unknown parameter: min_data_per_groups
[LightGBM] [Warning] Unknown parameter: min_data_per_groups
[LightGBM] [Warning] Unknown parameter: min_data_per_groups
[LightGBM] [Warning] Unknown parameter: min_data_per_groups
[LightGBM] [Warning] Unknown parameter: min_data_per_groups
[LightGBM] [Warning] Unknown parameter: min_data_per_groups
[LightGBM] [Warning] Unknown parameter: min_data_per_groups
[LightGBM] [Warning] Unknown parameter: min_data_per_groups
[LightGBM] [Warning] Unknown parameter: min_data_per_groups
[LightGBM] [Warning] Unknown parameter: min_data_per_groups
[LightGBM] [Warning] Unknown parameter: min_data_per_groups
[LightGBM] [Warning] Unknown parameter: min_data_per_groups
[LightGBM] [Warning] Unknown parameter: min_data_per_groups
[LightGBM] [Warning] Unknown parameter: min_data_per_groups
[LightGBM] [Warning] Unknown parameter: min_data_per_groups
[LightGBM] [Warning] Unknown parameter: 

20it [00:00, 37.38it/s]

...

2057it [00:57, 37.79it/s]

[LightGBM] [Warning] Unknown parameter: min_data_per_groups
[LightGBM] [Warning] Unknown parameter: min_data_per_groups
[LightGBM] [Warning] Unknown parameter: min_data_per_groups
[LightGBM] [Warning] Unknown parameter: min_data_per_groups
[LightGBM] [Warning] Unknown parameter: min_data_per_groups
[LightGBM] [Warning] Unknown parameter: min_data_per_groups
[LightGBM] [Warning] Unknown parameter: min_data_per_groups
[LightGBM] [Warning] Unknown parameter: min_data_per_groups
[LightGBM] [Warning] Unknown parameter: min_data_per_groups
[LightGBM] [Warning] Unknown parameter: min_data_per_groups
[LightGBM] [Warning] Unknown parameter: min_data_per_groups
[LightGBM] [Warning] Unknown parameter: min_data_per_groups
[LightGBM] [Warning] Unknown parameter: min_data_per_groups
[LightGBM] [Warning] Unknown parameter: min_data_per_groups
[LightGBM] [Warning] Unknown parameter: min_data_per_groups
[LightGBM] [Warning] Unknown parameter: min_data_per_groups
[LightGBM] [Warning] Unknown parameter: 

2066it [00:58, 39.11it/s]

[LightGBM] [Warning] Unknown parameter: min_data_per_groups
[LightGBM] [Warning] Unknown parameter: min_data_per_groups
[LightGBM] [Warning] Unknown parameter: min_data_per_groups
[LightGBM] [Warning] Unknown parameter: min_data_per_groups
[LightGBM] [Warning] Unknown parameter: min_data_per_groups
[LightGBM] [Warning] Unknown parameter: min_data_per_groups
[LightGBM] [Warning] Unknown parameter: min_data_per_groups
[LightGBM] [Warning] Unknown parameter: min_data_per_groups
[LightGBM] [Warning] Unknown parameter: min_data_per_groups
[LightGBM] [Warning] Unknown parameter: min_data_per_groups
[LightGBM] [Warning] Unknown parameter: min_data_per_groups
[LightGBM] [Warning] Unknown parameter: min_data_per_groups
[LightGBM] [Warning] Unknown parameter: min_data_per_groups
[LightGBM] [Warning] Unknown parameter: min_data_per_groups
[LightGBM] [Warning] Unknown parameter: min_data_per_groups
[LightGBM] [Warning] Unknown parameter: min_data_per_groups
[LightGBM] [Warning] Unknown parameter: 

2066it [00:58, 35.50it/s]
